In [3]:
import sys
sys.path += ['../..']

from data_collection.data_collection import LoggerSet, Logger

import numpy as np
import pandas as pd
import plotly.express as px
from data_collection.video_data import get_frame_iterator
from pathlib import Path
from typing import Iterable, Tuple, List
from tqdm import tqdm
import datetime
import tensorflow as tf
import tensorflow.keras as keras

%load_ext autoreload
%autoreload 2


2024-06-29 09:09:12.432422: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-06-29 09:09:13.281090: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


# Note
- Condition: same as test 7 but with less augmentation
- same level of augmentation but fixed errors in test 7 
- great result
-   can be directly used for the car control?

# Loading data 

In [5]:
from with_linear_acc import Session
sessions = Session.load_multiple_session('../data')
frames, df = Session.concatenate_multiple_sessions(sessions)

[mov,mp4,m4a,3gp,3g2,mj2 @ 0x576ddc9e6e40] moov atom not found


## Inspection only

In [6]:
df = sessions[0].data['angular_speed_control_df']

In [7]:

def mean_nominmax(x):
    return (x.sum()-x.max()-x.min())/(len(x)-2)
asd0 = df['angular_velocity'].rolling(100).apply(mean_nominmax).shift(-99)

asd = df['angular_velocity'].rolling(50).apply(mean_nominmax).shift(-49)
asd1 = df['angular_velocity'].rolling(3).apply(mean_nominmax).shift(-2)


px.line(y=[asd1, asd, asd0])

# Select data for the model

In [8]:
def prepare_to_tensorflow(frames, df):

    # data selection
    df = df.query('speed!=0')

    # match the data with the frame
    frame2data = df.groupby('exact_total_frame_idx')[['linacc0', 'linacc1', 'linacc2', 'speed']].mean()
    outputs = df.groupby('offset_total_frame_idx')[['left_smooth', 'right_smooth']].mean()

    # the reindexed data
    frame_indices = outputs.index.values

    frames_reindexed = frames[frame_indices]
    other_inputs = frame2data.reindex(frame_indices)

    # screen out the nans
    nafilter = (~other_inputs.isna().any(axis=1)).values

    frames_reindexed = frames_reindexed[nafilter]
    other_inputs = other_inputs.values[nafilter]
    outputs = outputs.values[nafilter]
    
    
    return frames_reindexed, other_inputs/10, outputs/100

In [9]:
frames_in, other_in, out = prepare_to_tensorflow(frames, df)

In [10]:

from train_tools import validation_chunk_split

In [11]:
train_idx, val_idx = validation_chunk_split(len(frames_in), val_split=0.2)
train_frames, train_other, train_out = frames_in[train_idx], other_in[train_idx], out[train_idx]
val_frames, val_other, val_out = frames_in[val_idx], other_in[val_idx], out[val_idx]

In [1]:
train_frames

NameError: name 'train_frames' is not defined

# Model

In [12]:
def get_model(lr=.1, other_metrics=[]):
    tf.keras.backend.clear_session()
    image_shape = 64, 114, 3

    img_aug_preprocess_layers = [
        keras.layers.RandomTranslation(0.05, 0.05, fill_mode='reflect'),
        keras.layers.RandomRotation(0.02, fill_mode='reflect'),
        keras.layers.RandomZoom(0.05, fill_mode='reflect'),
        keras.layers.RandomContrast(0.3),
        keras.layers.RandomBrightness(factor=0.6, value_range=[0, 1])
    ]
    
    cnn_layers =  [
        keras.layers.Conv2D(16, 5, strides=2, activation='relu'), 
        keras.layers.Conv2D(32, 5, strides=2, activation='relu'), 
        keras.layers.Conv2D(64, 5, strides=2, activation='relu'),         
        keras.layers.Conv2D(64, 3, activation='relu'), 
        keras.layers.Conv2D(96, 3, activation='relu'),         
        keras.layers.Flatten(),
        keras.layers.Dropout(0.2),
    ]
    
    cnn = keras.Sequential(
        [
            keras.layers.InputLayer(image_shape),
            keras.layers.Rescaling(1/255), 
            *img_aug_preprocess_layers,
            *cnn_layers
        ])

    other_inputs = keras.layers.InputLayer((4,))
    x = keras.layers.Concatenate()([cnn.outputs[0], other_inputs.output])
    x = keras.layers.Dense(128, activation='relu')(x)
    x = keras.layers.Dense(64, activation='relu')(x)
    y = keras.layers.Dense(2, activation='sigmoid')(x)

    model = keras.Model([cnn.inputs[0], other_inputs.output], y)


    optimiser = keras.optimizers.Adam(lr)
    model.compile(optimizer=optimiser, loss='Huber', metrics=['MAE']+other_metrics)

    return model 

model = get_model()
model.summary()

2024-06-29 09:10:09.319709: I external/local_xla/xla/stream_executor/cuda/cuda_executor.cc:998] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero. See more at https://github.com/torvalds/linux/blob/v6.0/Documentation/ABI/testing/sysfs-bus-pci#L344-L355
2024-06-29 09:10:09.491887: I external/local_xla/xla/stream_executor/cuda/cuda_executor.cc:998] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero. See more at https://github.com/torvalds/linux/blob/v6.0/Documentation/ABI/testing/sysfs-bus-pci#L344-L355
2024-06-29 09:10:09.492132: I external/local_xla/xla/stream_executor/cuda/cuda_executor.cc:998] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero. See more at https://github.com/torvalds/linux/blob/v6.0/Documentation/ABI/testing/sysfs-bus-pci#L344-

Model: "functional_2"

┏━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)        ┃ Output Shape      ┃    Param # ┃ Connected to      ┃
┡━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━┩
│ input_layer         │ (None, 64, 114,   │          0 │ -                 │
│ (InputLayer)        │ 3)                │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ rescaling           │ (None, 64, 114,   │          0 │ input_layer[0][0] │
│ (Rescaling)         │ 3)                │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ random_translation  │ (None, 64, 114,   │          0 │ rescaling[0][0]   │
│ (RandomTranslation) │ 3)                │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ random_rotation     │ (None, 64, 114,   │          0 │ random_translati… │
│ (RandomRotation)    │ 3)                │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ random_zoom         │ (None, 64, 114,   │          0 │ random_rotation[… │
│ (RandomZoom)        │ 3)                │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ random_contrast     │ (None, 64, 114,   │          0 │ random_zoom[0][0] │
│ (RandomContrast)    │ 3)                │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ random_brightness   │ (None, 64, 114,   │          0 │ random_contrast[… │
│ (RandomBrightness)  │ 3)                │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2d (Conv2D)     │ (None, 30, 55,    │      1,216 │ random_brightnes… │
│                     │ 16)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2d_1 (Conv2D)   │ (None, 13, 26,    │     12,832 │ conv2d[0][0]      │
│                     │ 32)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2d_2 (Conv2D)   │ (None, 5, 11, 64) │     51,264 │ conv2d_1[0][0]    │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2d_3 (Conv2D)   │ (None, 3, 9, 64)  │     36,928 │ conv2d_2[0][0]    │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2d_4 (Conv2D)   │ (None, 1, 7, 96)  │     55,392 │ conv2d_3[0][0]    │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ flatten (Flatten)   │ (None, 672)       │          0 │ conv2d_4[0][0]    │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dropout (Dropout)   │ (None, 672)       │          0 │ flatten[0][0]     │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ input_layer_1       │ (None, 4)         │          0 │ -                 │
│ (InputLayer)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ concatenate         │ (None, 676)       │          0 │ dropout[0][0],    │
│ (Concatenate)       │                   │            │ input_layer_1[0]… │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense (Dense)       │ (None, 128)       │     86,656 │ concatenate[0][0] │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense_1 (Dense)     │ (None, 64)        │      8,256 │ dense[0][0]       │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense_2 (Dense)     │ (None, 2)         │        130 │ dense_1[0][0]     │
└─────────────────────┴───────────────────┴────────────┴─────────────────

 Total params: 252,674 (987.01 KB)

 Trainable params: 252,674 (987.01 KB)

 Non-trainable params: 0 (0.00 B)

In [13]:
from train_tools import find_lr, tg_notify, use_tensorboard, end_epoch_notify

In [14]:
find_lr(get_model(), [train_frames, train_other], train_out)
#tensorboard --logdir src/training/logs --bind_all

Epoch 1/100


2024-06-29 09:10:18.676462: I external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:465] Loaded cuDNN version 8907


KeyboardInterrupt: 

In [15]:
model = get_model(2e-4)
model.fit(
    [train_frames, train_other],
    train_out,
    epochs=100, 
    validation_data = ([val_frames, val_other], val_out),
    callbacks=[
        tf.keras.callbacks.EarlyStopping(monitor='val_loss', patience=10),
        use_tensorboard('training'), 
        end_epoch_notify()
        ] 
    )

Epoch 1/100
160/160 ━━━━━━━━━━━━━━━━━━━━ 4s 12ms/step - MAE: 0.0944 - loss: 0.0073 - val_MAE: 0.0662 - val_loss: 0.0040
Epoch 2/100
160/160 ━━━━━━━━━━━━━━━━━━━━ 1s 9ms/step - MAE: 0.0660 - loss: 0.0039 - val_MAE: 0.0599 - val_loss: 0.0037
Epoch 3/100
160/160 ━━━━━━━━━━━━━━━━━━━━ 1s 8ms/step - MAE: 0.0625 - loss: 0.0038 - val_MAE: 0.0611 - val_loss: 0.0037
Epoch 4/100
160/160 ━━━━━━━━━━━━━━━━━━━━ 1s 9ms/step - MAE: 0.0607 - loss: 0.0036 - val_MAE: 0.0606 - val_loss: 0.0037
Epoch 5/100
160/160 ━━━━━━━━━━━━━━━━━━━━ 1s 8ms/step - MAE: 0.0596 - loss: 0.0035 - val_MAE: 0.0599 - val_loss: 0.0037
Epoch 6/100
160/160 ━━━━━━━━━━━━━━━━━━━━ 1s 8ms/step - MAE: 0.0594 - loss: 0.0035 - val_MAE: 0.0646 - val_loss: 0.0041
Epoch 7/100
160/160 ━━━━━━━━━━━━━━━━━━━━ 1s 8ms/step - MAE: 0.0594 - loss: 0.0035 - val_MAE: 0.0615 - val_loss: 0.0038
Epoch 8/100
160/160 ━━━━━━━━━━━━━━━━━━━━ 1s 8ms/step - MAE: 0.0597 - loss: 0.0036 - val_MAE: 0.0591 - val_loss: 0.0036
Epoch 9/100
160/160 ━━━━━━━━━━━━━━━━━━━━ 1s 8ms

In [ ]:
#frames_reindexed#, other_inputs_reindexed, outputs

# visualise the performance

In [16]:

#train_frames, train_other, train_out
val_idxv = np.sort(val_idx)
train_idxv = np.sort(train_idx)

val_y_pred = model.predict([frames_in[val_idxv], other_in[val_idxv]], batch_size=64)
train_y_pred = model.predict([frames_in[train_idxv], other_in[train_idxv]], batch_size=64)


val_outv = out[val_idxv]
train_outv = out[train_idxv]

px.line(np.c_[train_outv[:, :], train_y_pred[:, :]], title='train')

15/15 ━━━━━━━━━━━━━━━━━━━━ 0s 7ms/step
80/80 ━━━━━━━━━━━━━━━━━━━━ 0s 3ms/step


In [17]:
px.line(np.c_[val_outv[:, :], val_y_pred[:, :]], title='val')

In [18]:
#model.export('29Jun-export.keras')
model.save('29Jun-save.keras')


INFO:tensorflow:Assets written to: 29Jun-export.keras/assets


INFO:tensorflow:Assets written to: 29Jun-export.keras/assets


Saved artifact at '29Jun-export.keras'. The following endpoints are available:

* Endpoint 'serve'
  args_0 (POSITIONAL_ONLY): List[TensorSpec(shape=(None, 64, 114, 3), dtype=tf.float32, name='keras_tensor'), TensorSpec(shape=(None, 4), dtype=tf.float32, name='keras_tensor_14')]
Output Type:
  TensorSpec(shape=(None, 2), dtype=tf.float32, name=None)
Captures:
  132661077198624: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132661086693408: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132660136561472: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132660136570272: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132660136574144: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132660138343968: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132660138339216: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132660138342032: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132660138343792: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132660